In [1]:
import os
os.getcwd()
 
import pandas as pd
import numpy as np
import datetime
from dateutil.relativedelta import relativedelta
import matplotlib.pyplot as plt
from matplotlib import gridspec
import quantstats as qs
from pyecharts import Line, Bar, Scatter, Grid, Overlap
import plotly.figure_factory as ff
from statsmodels.formula.api import ols
import sqlite3
from tqdm import tqdm

In [2]:
con = sqlite3.connect("./Fin Lab/data/total.db")
cursor = con.cursor()
cursor.execute(f"SELECT * FROM total WHERE 날짜 >= 20100101")
data = cursor.fetchall()
df = pd.DataFrame(data, columns=['_', 
                                 '날짜','시가','고가','저가','종가','거래량',
                                 '거래대금','시가총액','수정주가비율','종목코드','거래소'])

In [3]:
df = df.drop('_', axis=1)

In [4]:
def Get_Signal(date, code):
    _df = df[df['종목코드']==code]
    
    _df['MA120'] = _df['종가'].rolling(window=5, min_periods=5).mean()

    _df.fillna(0, inplace=True)
    _df['high<MA'] = _df['고가'] < _df['MA120']

#     _df['is20'] = np.nan
    
    _df = _df.reset_index()
    Numdata = len(_df)
    
#     tmp=0
#     _df['continue'] = _df['high<MA'].shift(2) * _df['high<MA'].shift(1)
    _df['continue'] = _df['high<MA'].shift(1)*1
#     for idx in range(2, Numdata):

#         if _df['high<MA'].iloc[idx-1] == True and _df['high<MA'].iloc[idx-2] == True :
#             tmp += 1
#         else:
#             tmp = 0

#         if tmp >= 1:
#             _df.iloc[idx, -1] = 1
#         else:
#             _df.iloc[idx, -1] = 0

#     _df.dropna(inplace=True)
    Numdata = len(_df)
    _df['Buy'] = 0

    for idx in range(Numdata):
        # 해당일자 저가가 이평선 120일보다 낮아야하고 고가가 이평선 120일보다 높아야함
        if _df['continue'].iloc[idx] == 1:        
            if _df['저가'].iloc[idx] <= _df['MA120'].iloc[idx] and _df['고가'].iloc[idx] >= _df['MA120'].iloc[idx]:
                _df.iloc[idx, -1] = 1
            else:
                _df.iloc[idx, -1] = 0
        else:
            _df.iloc[idx, -1] = 0
            
#         if len(_df[_df['날짜']==date]) == 0:
#             return 0

# _df[_df['날짜']==date]['Buy'].values[0]

    _df = _df[_df['날짜']==date]

#     display(_df[_df['날짜']==date])
    
    if len(_df) == 0:
        return 0

    return _df[_df['날짜']==date]['Buy'].values[0]

In [5]:
def Get_date(date):
    _df = df[df['날짜']==date]
#     _df = _df[_df['거래량']>5000000]
    _df = _df[_df['거래소']=='KOSDAQ']
    _df['bs'] = 0
    _df = _df.reset_index()
    
    bs_list = []
    
    for idx, row in _df.iterrows():
        bs_list.append(Get_Signal(date, row['종목코드']))
       
    _df['bs'] = bs_list
    return _df.sort_values(by='거래량', ascending=False)

In [6]:
df = df[df['거래량']>10000000]
df = df[df['거래소']=='KOSDAQ'].sort_values(by='날짜', ascending=False)
Money = 10000000
Money_list = []
total_list = []
Account = pd.DataFrame()
for date in tqdm(sorted(df['날짜'].unique())):
    result = Get_date(date)
    Money_list.append(Money)
    if len(Account) < 10 :
        if len(result) == 0 :
            pass
        else :  
            for idx in result[result['bs']==1].index:
                Account = Account.append({'날짜' :  round(result[result['bs']==1]['날짜'][idx],0),'종목코드' : result[result['bs']==1]['종목코드'][idx],'매입가' : result[result['bs']==1]['종가'][idx], '수량' : (Money/10)//result[result['bs']==1]['종가'][idx]} , ignore_index=True)
                Money -= (result[result['bs']==1]['종가'][idx])*((Money/10)//result[result['bs']==1]['종가'][idx])
                print("채결 \n 종목:", result[result['bs']==1]['종목코드'][idx], "   일자:", result[result['bs']==1]['날짜'][idx], "   매입가:", result[result['bs']==1]['종가'][idx], "   수량:", (Money/10)//result[result['bs']==1]['종가'][idx], "   잔고:", Money)
    else : 
        pass
    
    for i in Account.index:
        condition1 = df['날짜']==Account['날짜'][i]
        condition2 = df['종목코드']==Account['종목코드'][i]
        FOC = (((df[condition1 & condition2]['시가'].iloc[0] / Account['매입가'][i]) - 1) - 0.0038 > 0.1)
        if FOC == True :
            Money += df[condition1 & condition2]['시가'].iloc[0] * Account['수량'][i] * (1-0.0038)
            print("채결 \n 종목:", Account['종목코드'][i], "   일자:", Account['날짜'][i], "   매도가:", df[condition1 & condition2]['시가'].iloc[0], "   수량:", Account['수량'][i], "   잔고: ", Money)
            Account = Account.drop(i)
        elif (date - Account['날짜'][i]) > 5:
            Money += df[condition1 & condition2]['시가'].iloc[0] * Account['수량'][i] * (1-0.0038)
            print("채결 \n 종목:", Account['종목코드'][i], "   일자:", Account['날짜'][i], "   매도가:", df[condition1 & condition2]['시가'].iloc[0], "   수량:", Account['수량'][i], "   잔고: ", Money)
            Account = Account.drop(i)
    display("일일정산:",Account)
    display("현금:", Money)
    if len(Account) > 0 :
        total = Money + (Account['매입가']*Account['수량']).sum()
    else :
        total = Money
    total_list.append(total)
    display("총 자산가치:", total)  

  0%|                                                                                         | 0/2565 [00:00<?, ?it/s]

'일일정산:'

Empty DataFrame
Columns: []
Index: []

'현금:'

10000000

...

'현금:'

41334233.612399936

'총 자산가치:'

41334233.612399936

100%|██████████████████████████████████████████████████████████████████████████████| 2565/2565 [24:00<00:00,  1.78it/s]
